In [0]:
# Import required libraries
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, trim, lower, upper, initcap, length, regexp_replace, avg, count

# Start Spark session
spark = SparkSession.builder.appName("Goodreads Cleaning Gold Layer").getOrCreate()


In [0]:
# ===============================
# Load curated dataset (Delta)
# ===============================

# Authentication (keep your SAS settings from earlier here)
spark.conf.set(
    "fs.azure.account.auth.type.goodreadsreviewsgen2.dfs.core.windows.net", "SAS")
spark.conf.set(
    "fs.azure.sas.token.provider.type.goodreadsreviewsgen2.dfs.core.windows.net",
    "org.apache.hadoop.fs.azurebfs.sas.FixedSASTokenProvider")
spark.conf.set(
    "fs.azure.sas.fixed.token.goodreadsreviewsgen2.dfs.core.windows.net",
    "sp=rl&st=2025-11-10T16:31:14Z&se=2025-11-11T00:46:14Z&spr=https&sv=2024-11-04&sr=c&sig=7ObMZmTF7%2BsuRdomnRUyJvCoLHZESZlSbvTtzwA2goY%3D"
)

# Read dataset as Delta instead of Parquet
df = spark.read.format("delta").load(
    "abfss://lakehouse@goodreadsreviewsgen2.dfs.core.windows.net/gold/curated_reviews"
)

# Display the data
display(df)


review_id book_id title author_id name user_id rating review_text n_votes date_added 56d3bfe96ef9ed0b14cd1fe5a981150e 20566082 A Kitty in the Lion's Den (Sweet Water, #3) 604031 Ronald J. Fields 6909165b2c5b492a56c052d96c408ae1 4 3.5 Lots of sex and violence! Exactly what I want when I pick up a JS book. 0 Fri Jan 08 16:59:51 -0800 2016 396b842d094b11e8e0de9526943ea2ae 17279616 Štyri hostiny 604031 Ronald J. Fields 918b32591b04968a9afb560bdc9833c4 4 Kupila som si tuto knizku len preto, aby som mala nieco "intelektualskejsie" na citanie pri vsetkych detektivkach a historickych romanoch. Ale bol to skvely vyber. 
 Chvilu som ju nechala doma odpocivat a az neskor som sa pustila do styroch hostin, na ktore pozyva Jakob Seinfeld chlapca Zajdeho. Jeden z troch otcov svojho syna. Traja otcovia, jeden syn? Vselico sa stava a nic nie je nemozne. Aspon nie v tomto spolocenskom romane od Meira Shaleva. 
 Musim priznat, ze mi trvalo dlhsie, kym som sa zacitala a knizka nema "grady", skor si tak plynie. Treba jej dat sancu, ma svoje caro. 
 Poziciam si uryvok (jemne ale len jemne spoilerovy): 
 "Rozpravka o lejaku, o vode stupajucej vo vadi, o klamarskom revizionistovi, o manzelovi, ktory otala, a o manzelke, ktora bola neverna, prisla o dceru a prisla zit a pracovat do mastale vdovca, ktoreho kravy dojila a ktoreho deti vychovavala... 
 Rozpravka o handliarovi, ktory nevie soferovat, o dietati, nad ktorym nema vladu smrt ani ziadostivost, o papierovych lodkach, o odstrihnutom vrkoci... 
 No vrkoc bol schovany, had ustipol, albin prisiel, klamar klamal, manzel otalal, zena otehotnela a tam, v mastali, zila, pracovala, spala, plakala a porodila syna, nad ktorym smrt nemala vladu... 
 Samozrejme, ze to tak bolo. Ak to tak nebolo, tak teda ako?" 
 Pribeh o vasni a o ludskom osude sa pise na zadnej obalke. A nic viac k tomu netreba. 2 Thu Mar 24 05:25:34 -0700 2016 48791f72b34f076a6c1ac944b04b9bda 12349663 Naoki Urasawa's 20th Century Boys, Volume 19 (20th Century Boys, #19) 604031 Ronald J. Fields 997c4810e3a16bcad347c6455d1625e5 3 This series is getting close to the end, you can feel the build-up, but sadly the long coming revelation and return of the main character Kenji felt a bit trite and predictable. Ok, so the whole of 20th Century Boys is very contrived and written to keep the suspense going seemingly for ever, but the simple and overused explanation of amnesia felt like too much of a gimmick. Maybe it's yet another homage to Japanese popular culture, but I must admit to feeling a bit disappointed... 
 Oh well, onward to the last few volumes. 0 Wed Oct 23 00:42:02 -0700 2013 47ff25e965e3fc8422595bf6be804ad6 1403505 The Pity Party: 8th Grade in the Life of Me, Cass 604031 Ronald J. Fields 0e62ee0b7d9061398472a6fa9884293c 5 I liked this book, but it didn't sound as if it took place in 1982 0 Sun Oct 25 14:36:40 -0700 2009 77ccc576a568543e7f73d6dd041a1ab2 25402549 The Possession of Lawrence Eugene Davis 604031 Ronald J. Fields 02db8f5a7c61e788d2f2f6638301d45f 4 Possession is my first book by E. E. Ottoman and only my second from this publisher. The title and description just caught my attention. I am always looking for a different take on the classic paranormal romance book. I enjoyed the historical events like the dust bowl and World War references. 
 I wish I could have learned more about Lawrence before the actual action of the novel began. I wanted to be more involved with his character before he is faced with the possession. 
 I like the twists and turn of the story. The different paranormal aspects was interesting. 0 Tue Aug 25 14:38:39 -0700 2015 d929ca1000f9b057bb65ec80e4bd4e60 1626346 Das Schlimmste kommt noch oder Fast eine Jugend 604031 Ronald J. Fields 29e263fab9ac7d09d9b601a846f78a09 4 Gut geschriebenes Buch ohne unerwartete Wendungen oder grosse Gedanken. Schreibweise ist flussig und melancholisch umgesetzt. Passend zum Inhalt. 
 Weiteres kann ich empfehlen fur diese Epoche. 
 Das schweigen des Lichtes- Niel Flemming 
 The 

In [0]:
df = df.dropna(subset=["rating", "review_text", "book_id", "author_id"])


In [0]:
df = df.dropDuplicates(["review_id"])
df = df.dropDuplicates(["user_id", "book_id"])


In [0]:
from pyspark.sql.functions import trim, lower

df = df.withColumn("review_text", trim(lower(df.review_text)))
df = df.withColumn("title", trim(lower(df.title)))
df = df.withColumn("name", trim(lower(df.name)))


In [0]:
from pyspark.sql.functions import length

df = df.withColumn("review_length", length(df.review_text))
df = df.filter(df.review_length >= 10)


In [0]:
df.select("rating", "n_votes").summary().show()


+-------+------------------+-----------------+
|summary|            rating|          n_votes|
+-------+------------------+-----------------+
|  count|              7516|             7516|
|   mean|3.6768227780734435|1.163650878126663|
| stddev|1.2797622517028802|5.754071825311664|
|    min|                 0|               -2|
|    25%|                 3|                0|
|    50%|                 4|                0|
|    75%|                 5|                1|
|    max|                 5|              208|
+-------+------------------+-----------------+



In [0]:
from pyspark.sql.functions import avg, count

agg_df = df.groupBy("book_id").agg(
    avg("rating").alias("avg_rating_per_book"),
    count("review_id").alias("num_reviews")
)
display(agg_df)


book_id avg_rating_per_book num_reviews 20566082 4.0 1 25402549 4.285714285714286 7 13648085 2.75 8 780912 3.25 4 218094 3.0 1 18628484 4.571428571428571 7 581166 3.0 2 9848978 5.0 1 2168736 3.4285714285714284 7 26201145 4.666666666666667 3 8845714 3.0 3 7943805 3.6666666666666665 3 19192696 4.5 2 4541271 3.0 4 23246799 5.0 2 13082921 3.5 4 18634986 3.888888888888889 36 12458821 3.3125 16 33022718 3.843137254901961 51 33355016 4.7272727272727275 11 16066754 2.0 1 20426739 4.0 6 16034998 4.5 2 12458829 3.375 16 12719273 4.538461538461538 13 11731784 4.5 2 10192420 3.2857142857142856 7 8364795 5.0 1 1477670 4.0 2 16174656 4.0 2 21243290 1.0 1 29391170 5.0 1 16250765 3.0 2 18711342 4.153846153846154 65 175243 3.8783783783783785 74 4507203 3.537313432835821 67 30056199 4.0 6 25421507 4.25 4 28144874 4.166666666666667 6 17575466 3.0 2 7843586 3.8 55 388674 3.45 20 89379 4.428571428571429 7 1698376 3.0 1 16138077 4.36 25 1393555 5.0 1 13110467 3.4 10 27879034 5.0 1 23815926 2.0 2 3209319 3.5714285714285716 7 38562 3.7551020408163267 98 22600550 3.8095238095238093 21 8425263 4.571428571428571 7 18389080 4.0 2 175248 3.5396825396825395 63 6282355 0.0 1 15774732 4.2 5 22061330 5.0 1 16114777 4.285714285714286 7 18192847 5.0 2 6066819 3.007142857142857 420 11827783 2.75 8 25501128 4.467741935483871 62 23615339 4.333333333333333 24 31622344 4.65625 32 25205644 4.2631578947368425 19 18498572 4.0 7 21401188 4.625 8 6453923 4.75 4 13231865 4.333333333333333 3 2741850 4.090909090909091 11 16693030 4.0 3 20613514 3.8 5 32065872 4.4 5 17909253 5.0 5 828180 3.5384615384615383 13 17313129 3.5 2 968456 3.2857142857142856 7 23615331 4.0 3 25518199 4.0 1 820226 4.0 10 54276 3.6666666666666665 6 268464 3.7058823529411766 17 8529354 3.6666666666666665 3 20650677 3.830769230769231 65 26864719 3.5098039215686274 102 30525379 4.0 9 17252158 3.0 4 29345617 4.526315789473684 19 10806004 2.230769230769231 13 22701782 4.0 5 7075301 4.0 1 30838933 3.8 5 27419760 4.0 2 17510247 3.0 1 218099 4.0 5 9036325 4.055555555555555 18 12106356 4.4 5 13643933 4.166666666666667 6 8244283 4.333333333333333 12 54270 2.215767634854772 241 31685294 4.8 5 218097 4.2 5 12725797 4.0 4 287149 3.0 4 25414989 3.0 1 17668619 4.0 34 1488663 4.5 10 378460 5.0 1 6452080 4.0 2 755063 5.0 1 268469 3.4 5 1907184 3.4285714285714284 14 346383 4.0 2 15900897 3.6666666666666665 6 30515690 5.0 1 19012266 3.0 1 9176116 4.0 9 6468516 5.0 1 31144338 5.0 1 30838930 1.0 1 6066812 3.0 1 20613515 4.222222222222222 9 18663972 3.909090909090909 22 34910950 4.0 1 19256674 3.0 1 27220739 3.7777777777777777 9 20613513 4.0 1 11731786 3.6 5 388678 4.333333333333333 6 828189 4.5 2 7815674 4.5 2 17405342 4.333333333333333 3 1167728 4.0 4 27859395 2.6 5 27220730 4.5 28 28950979 5.0 3 246205 3.6666666666666665 3 18819853 5.0 1 12597209 3.0714285714285716 14 32855795 4.333333333333333 6 25181937 4.555555555555555 9 25162658 3.5 4 243804 3.0 1 33833122 4.571428571428571 7 23010495 4.0 1 22161927 1.0 1 29074693 4.75 4 23301510 4.0 1 13382196 4.0 2 30309543 4.0 2 18908446 4.0 5 14287198 4.0 1 591284 3.5 6 12388481 5.0 7 20613512 3.25 4 23992420 4.333333333333333 3 22889750 3.5454545454545454 55 32615013 4.5 4 977525 3.0 1 27189834 3.0 1 27693272 4.2272727272727275 22 14305822 1.0 1 13598469 2.0 1 2657344 4.0 1 27036535 4.0 1 25096548 4.0 1 22736662 4.8 5 23217086 4.476190476190476 21 10313894 4.75 8 15861985 3.6666666666666665 3 23301515 5.0 1 16074814 3.3076923076923075 13 18362696 5.0 1 105639 4.0 2 20650678 4.28125 32 17175207 4.363636363636363 11 36171424 5.0 3 30971685 4.232323232323233 99 2741853 3.3846153846153846 78 32615012 5.0 1 33809724 5.0 1 29074697 2.0 1 926667 4.0 3 17668616 5.0 1 16111978 4.0 2 2437856 5.0 1 22796932 3.0 1 15837689 3.5 6 35046085 3.0 1 981692 2.6666666666666665 3 13519484 4.285714285714286 7 13519488 3.9285714285714284 14 13579397 3.3684210526315788 19 23825456 4.0 3 10315513 4.0 1 780917 2.857142857142857 14 10066326 3.3333333333333335 3 27220736 4.412280701754386 228 18593020 3.3

In [0]:
# 1) Point to your Gold root once
gold_root = "abfss://lakehouse@goodreadsreviewsgen2.dfs.core.windows.net/gold"
target    = f"{gold_root}/features_v1"

# 2) (Optional) See what's there
display(dbutils.fs.ls(gold_root))

path name size modificationTime abfss://lakehouse@goodreadsreviewsgen2.dfs.core.windows.net/gold/curated_reviews/ curated_reviews/ 0 1762195834000

In [0]:
# Write features to Databricks internal storage instead of ADLS
(agg_df
    .write
    .format("delta")
    .mode("overwrite")
    .option("overwriteSchema", "true")
    .save("/mnt/tmp/features_v1")
)

print("✅ Successfully written locally to /mnt/tmp/features_v1")


✅ Successfully written locally to /mnt/tmp/features_v1


In [0]:
display(spark.read.format("delta").load("/mnt/tmp/features_v1"))


book_id avg_rating_per_book num_reviews 25402549 4.285714285714286 7 780912 3.25 4 18628484 4.571428571428571 7 2471304 4.0 1 23246792 3.5 4 13340336 3.0 1 2168736 3.4285714285714284 7 23246799 5.0 2 831611 3.0 1 7943805 3.6666666666666665 3 34680604 5.0 5 13082921 3.5 4 18634986 3.888888888888889 36 12458821 3.3125 16 351696 4.0 4 13519483 3.0 1 8730988 4.333333333333333 3 33355016 4.7272727272727275 11 33022718 3.843137254901961 51 20426739 4.0 6 27255991 5.0 1 12458829 3.375 16 17991730 4.0 1 16174656 4.0 2 1477670 4.0 2 4507203 3.537313432835821 67 175243 3.8783783783783785 74 18711342 4.153846153846154 65 30056199 4.0 6 25421507 4.25 4 28144874 4.166666666666667 6 24494834 5.0 2 7843586 3.8 55 15837688 5.0 1 388674 3.45 20 1907185 1.6666666666666667 3 16138077 4.36 25 13110467 3.4 10 31124999 4.0 1 2805495 3.0 2 13340338 5.0 1 17373671 5.0 1 3209319 3.5714285714285716 7 38562 3.7551020408163267 98 8425263 4.571428571428571 7 26106944 4.0 4 22600550 3.8095238095238093 21 18192847 5.0 2 175248 3.5396825396825395 63 15774732 4.2 5 16114777 4.285714285714286 7 6066819 3.007142857142857 420 11827783 2.75 8 25205644 4.2631578947368425 19 31622344 4.65625 32 25501128 4.467741935483871 62 23615339 4.333333333333333 24 18498572 4.0 7 2741850 4.090909090909091 11 6453923 4.75 4 218093 2.0 2 21401188 4.625 8 17368265 3.8333333333333335 6 32065872 4.4 5 17909253 5.0 5 977529 4.142857142857143 7 828180 3.5384615384615383 13 16084759 4.0 2 968456 3.2857142857142856 7 820226 4.0 10 268464 3.7058823529411766 17 8529354 3.6666666666666665 3 26864719 3.5098039215686274 102 20650677 3.830769230769231 65 21771068 5.0 1 8307481 4.0 2 34104667 3.6 5 29345617 4.526315789473684 19 10806004 2.230769230769231 13 22701782 4.0 5 18628480 4.5 6 12349665 4.666666666666667 3 30838933 3.8 5 19541858 4.333333333333333 6 13643933 4.166666666666667 6 6719824 3.0 2 12106356 4.4 5 9036325 4.055555555555555 18 8244283 4.333333333333333 12 246200 4.0 1 17681424 5.0 1 31685294 4.8 5 54270 2.215767634854772 241 218097 4.2 5 1641083 2.6666666666666665 3 17668619 4.0 34 1488663 4.5 10 6719823 3.0 2 1877618 4.333333333333333 3 1907184 3.4285714285714284 14 24614930 4.0 3 9176116 4.0 9 15900897 3.6666666666666665 6 28094336 3.0 1 20613515 4.222222222222222 9 581169 5.0 1 12996838 2.0 1 785553 3.8333333333333335 6 2097274 4.0 1 18663972 3.909090909090909 22 27220739 3.7777777777777777 9 388678 4.333333333333333 6 24489718 3.0 1 1167728 4.0 4 27859395 2.6 5 27220730 4.5 28 10290982 3.875 8 28950979 5.0 3 1517589 4.125 8 316999 5.0 1 12597209 3.0714285714285716 14 25181937 4.555555555555555 9 32317913 4.666666666666667 3 18624033 5.0 1 3281038 4.0 1 23716534 4.0 3 33833122 4.571428571428571 7 958987 4.0 1 29074693 4.75 4 348524 4.0 1 27036537 5.0 1 18908446 4.0 5 591284 3.5 6 23992420 4.333333333333333 3 581162 3.0 1 22889750 3.5454545454545454 55 27693272 4.2272727272727275 22 34893712 4.2 5 23615336 3.0 1 31291952 4.0 2 20882013 3.0 1 23217086 4.476190476190476 21 29940158 4.5 6 10313894 4.75 8 16074814 3.3076923076923075 13 18192846 2.8 5 20650678 4.28125 32 17175207 4.363636363636363 11 30971685 4.232323232323233 99 2741853 3.3846153846153846 78 26791581 3.0 1 20613519 3.5 8 9402756 4.0 1 13519484 4.285714285714286 7 15837689 3.5 6 13519488 3.9285714285714284 14 31124994 3.0 2 780917 2.857142857142857 14 13579397 3.3684210526315788 19 23825456 4.0 3 10066326 3.3333333333333335 3 27220736 4.412280701754386 228 18593020 3.3076923076923075 13 20613511 3.883720930232558 172 19016508 4.6 5 18634982 2.9225352112676055 142 22499086 5.0 1 29862816 4.0 1 38565 3.2 10 6719825 1.5 2 19396714 3.0 2 28436751 2.6 5 18628482 4.666666666666667 6 1263548 4.0 2 8037411 5.0 1 10192426 4.0 4 34320236 4.285714285714286 42 11731782 3.357142857142857 98 15843134 3.857142857142857 14 6359544 4.5 12 1409922 4.0 1 175247 3.7936507936507935 63 6590855 4.0 1 18527178 3.25 4 9463563 3.7 60 32970513 3.6666666666666665 3 18134258 2.0 1 35568287 2.6666666666666665 3 780918 3.0 5 105638 3.71428571

In [0]:
# Load and verify the final Gold dataset (local Databricks storage)
check_df = spark.read.format("delta").load("/mnt/tmp/features_v1")

# Display a sample of records to confirm structure and values
display(check_df.limit(10))


book_id avg_rating_per_book num_reviews 25402549 4.285714285714286 7 780912 3.25 4 18628484 4.571428571428571 7 2471304 4.0 1 23246792 3.5 4 13340336 3.0 1 2168736 3.4285714285714284 7 23246799 5.0 2 831611 3.0 1 7943805 3.6666666666666665 3